In [1]:
import pandas as pd
import nltk
import scipy.stats
import sklearn
import numpy

In [2]:
data = pd.read_csv('./CSVs/V1/DODFCorpus_contratos_licitacoes_v1.csv', dtype=str)

In [3]:
#Insere um espaço entre as entidade e :
import re
def correct_space_before_numeric_entities(string):
    result = re.sub(r'([A-Za-z]:)[0-9]', r'\1 ', string)
    result = result.replace("\n", " ")
    return result

In [4]:

#Preprocessa o dataset para ajustar o casos de entidade e : sem espaço
#df['a']=df['a'].map(func)
#data['texto']= data['texto'].apply(result)
data['texto']= data['texto'].map(correct_space_before_numeric_entities)


In [5]:
data['id_ato'] = data['id_dodf'] + '-' + data['id_rel']
#data

In [6]:
result = data.groupby('tipo_rel')['id_ato'].nunique()
print(result.sort_values(ascending=False))

tipo_rel
REL_EXTRATO_CONTRATO        1542
REL_ADITAMENTO_CONTRATO     1537
REL_AVISO_LICITACAO          638
REL_SUSPENSAO_LICITACAO       68
REL_ANUL_REVOG_LICITACAO      46
REL_EXTRATO_CONVENIO          24
Name: id_ato, dtype: int64


In [7]:
tipo_ato = data.loc[data['tipo_rel'] == 'REL_AVISO_LICITACAO'].reset_index(drop=True)
#tipo_ato.to_csv("./CSVs/V1/REL_AVISO_LICITACAO.csv")
#tipo_ato

In [8]:
result = tipo_ato.groupby('tipo_ent')['id_ato'].nunique()
print(result)
#print(result.sort_values(ascending=False))

tipo_ent
AVISO_LICITACAO                     638
codigo_licitacao_sistema_compras    439
data_abertura_licitacao             626
modalidade_licitacao                610
nome_responsavel                    627
numero_licitacao                    635
objeto_licitacao                    633
orgao_licitante                     481
processo_gdf                        611
sistema_compras                     566
tipo_objeto                         622
valor_estimado_contratacao          474
Name: id_ato, dtype: int64


In [9]:
#apenas para rodar o iob com spacy
#cria um novo dataset com as 2000 primeiras linhas
#tipo_ato = pd.read_csv("./CSVs/V1//REL_AVISO_LICITACAO.csv", nrows=2000)

In [10]:
#cria um novo dataset apenas com o tipo de entidade EXTATO_CONTRATO (TEXTO)
tipo_ato1 = tipo_ato.loc[tipo_ato['tipo_ent'] == 'AVISO_LICITACAO'].reset_index(drop=True)
tipo_ato1


Unnamed: 0        id_dodf             tipo_rel id_rel       anotador_rel  \
0            9  12_22.11.2018  REL_AVISO_LICITACAO    R21  anotador_22346437   
1           19  12_22.11.2018  REL_AVISO_LICITACAO    R22  anotador_22346437   
2           30  12_22.11.2018  REL_AVISO_LICITACAO    R23  anotador_22346437   
3           42  12_22.11.2018  REL_AVISO_LICITACAO    R24  anotador_22346437   
4           59  12_22.11.2018  REL_AVISO_LICITACAO    R25  anotador_22346437   
..         ...            ...                  ...    ...                ...   
633      40293            638  REL_AVISO_LICITACAO    R18  anotador_57860312   
634      40359            638  REL_AVISO_LICITACAO    R19  anotador_57860312   
635      40558            638  REL_AVISO_LICITACAO    R20  anotador_57860312   
636      40713            638  REL_AVISO_LICITACAO    R21  anotador_57860312   
637      40998            638  REL_AVISO_LICITACAO    R22  anotador_57860312   

            tipo_ent id_ent       anotador_ent  offset length  \
0    AVISO_LICITACAO    494  anotador_22346437  432830   1023   
1    AVISO_LICITACAO    496  anotador_22346437  433852    837   
2    AVISO_LICITACAO    499  anotador_22346437  435489    980   
3    AVISO_LICITACAO    500  anotador_22346437  436468   2010   
4    AVISO_LICITACAO    504  anotador_22346437  484402    962   
..               ...    ...                ...     ...    ...   
633  AVISO_LICITACAO   3375  anotador_57860312   95350   1737   
634  AVISO_LICITACAO   3387  anotador_57860312  108543   1211   
635  AVISO_LICITACAO   3400  anotador_57860312  139489   1155   
636  AVISO_LICITACAO   3922  anotador_57860312  153612   1545   
637  AVISO_LICITACAO   3924  anotador_57860312  190893   1348   

                                                 texto             id_ato  
0    AVISOS DE LICITACOES PREGAO ELETRONICO No 116/...  12_22.11.2018-R21  
1    PREGAO ELETRONICO No 129/2018 OBJETO: Registro...  12_22.11.2018-R22  
2    AVISOS DE LICITACOES PREGAO ELETRONICO No 141/...  12_22.11.2018-R23  
3    PREGAO ELETRONICO No 142/2018-UASG 925041 Obje...  12_22.11.2018-R24  
4    AVISO DE ABERTURA PREGAO ELETRONICO POR SRP No...  12_22.11.2018-R25  
..                                                 ...                ...  
633  AVISO DE RETIFICAÇÃO (*) CONCORRÊNCIA Nº 003/2...            638-R18  
634  AVISO CONCORRÊNCIA Nº 02/2022    Processo:    ...            638-R19  
635  AVISO DE LICITAÇÃO PREGÃO ELETRÔNICO Nº 07/202...            638-R20  
636  AVISO DE LICITAÇÃO - CONCORRÊNCIA Nº 03/2022 A...            638-R21  
637  AVISO DE RETOMADA DA LICITAÇÃO Concorrência nº...            638-R22  

[638 rows x 12 columns]

In [11]:
#criando novo dataframe somente com os textos
df = tipo_ato1['texto'].reset_index(drop=True)
df

0      AVISOS DE LICITACOES PREGAO ELETRONICO No 116/...
1      PREGAO ELETRONICO No 129/2018 OBJETO: Registro...
2      AVISOS DE LICITACOES PREGAO ELETRONICO No 141/...
3      PREGAO ELETRONICO No 142/2018-UASG 925041 Obje...
4      AVISO DE ABERTURA PREGAO ELETRONICO POR SRP No...
                             ...                        
633    AVISO DE RETIFICAÇÃO (*) CONCORRÊNCIA Nº 003/2...
634    AVISO CONCORRÊNCIA Nº 02/2022    Processo:    ...
635    AVISO DE LICITAÇÃO PREGÃO ELETRÔNICO Nº 07/202...
636    AVISO DE LICITAÇÃO - CONCORRÊNCIA Nº 03/2022 A...
637    AVISO DE RETOMADA DA LICITAÇÃO Concorrência nº...
Name: texto, Length: 638, dtype: object

In [12]:
#df.to_csv("./CSVs/REL_SUSPENSAO_LICITACAO_COMPLETO_TEXTO_V1.csv")

In [13]:
# CODIGO RESPONSAVEL PELA LIMPEZA DO TEXTO DA BASE OURO
import re

df1 =[]

for i in df:
    i = i.replace("\n", " ")
    i = re.sub('xx[a-z]{1,10}', '', i)
    #i = i.replace(r"xx[a-z]{1,10}","")
    aux = ' '.join(i.split())
    #print(aux)
    df1.append(aux)


In [14]:
len(df1)

638

In [15]:
""" ## Carrega o Teste para aplicação da LB direto
df_sk = pd.read_csv('./CSVs/Extrato_Contrato_Split_4_x_test_texto.csv', dtype=str)
df_sk """

" ## Carrega o Teste para aplicação da LB direto\ndf_sk = pd.read_csv('./CSVs/Extrato_Contrato_Split_4_x_test_texto.csv', dtype=str)\ndf_sk "

In [16]:
""" #criando novo dataframe de test somente com os textos
df_sk = df_sk['Texto'].reset_index(drop=True)
df_sk """

" #criando novo dataframe de test somente com os textos\ndf_sk = df_sk['Texto'].reset_index(drop=True)\ndf_sk "

In [17]:
# CODIGO DE APLICACAO DA SUPERVISAO FRACA
#Para rodar extrato de contrato
#import dodfSkweak_v1_2
#skw = dodfSkweak_v1_2.SkweakContratos(df1)

#Para rodar aditamento de contrato 
#import dodfSkweak_Aditamento
#skw = dodfSkweak_Aditamento.SkweakAditamento(df1)

#Para rodar Suspensao 
#import dodfSkweak_Suspensao
#skw = dodfSkweak_Suspensao.SkweakSuspensao(df1)

#Para rodar Anulacao e Revogação
#import dodfSkweak_Anul_Revog
#skw = dodfSkweak_Anul_Revog.SkweakAnulRevog(df1)

#Para rodar Aviso Licitação
import dodfSkweak_Aviso_Licitacao
skw = dodfSkweak_Aviso_Licitacao.SkweakAvisoLicitacao(df1)

skw.apply_label_functions()
skw.train_HMM_Dodf()

/Users/lucelia/Documents/GitHub/experiments/members/lucelia/venv/lib/python3.9/site-packages/tqdm/auto.py:22: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
/Users/lucelia/Documents/GitHub/experiments/members/lucelia/venv/lib/python3.9/site-packages/spacy/language.py:1895: UserWarning: [W123] Argument disable with value ['ner', 'lemmatizer'] is used instead of ['senter'] as specified in the config. Be aware that this might affect other components in your pipeline.
  warnings.warn(


Starting iteration 1
Finished E-step with 638 documents
Starting iteration 2


         1      -15900.2044             +nan


Finished E-step with 638 documents
Starting iteration 3


         2      -15193.8999        +706.3044


Finished E-step with 638 documents
Starting iteration 4


         3      -15183.1754         +10.7246


Finished E-step with 638 documents


         4      -15178.6519          +4.5235


Write to ./data/aviso_licitacao.spacy...done


In [18]:
#skw.list_spans_all()
skw.list_spans_specific(0)

[PREGAO ELETRONICO, 116/2018, 767.907,37, 00410-00024534/2017-65]


In [19]:
data_label=skw.get_hmm_dataframe()
data_label

processo_gdf modalidade_licitacao numero_licitacao  \
0        00410-00024534/2017-65    PREGAO ELETRONICO         116/2018   
1        00410-00010748/2018-35    PREGAO ELETRONICO         129/2018   
2    00410-00012776/2018-97-SCG    PREGAO ELETRONICO             141/   
3                            61    Pregao Eletronico         071/2018   
4        00060.00257811/2018-02    PREGAO ELETRONICO         488/2018   
..                          ...                  ...              ...   
633      00113-00002946/2022-66                              003/2022   
634      00113-00003425/2021-45                              002/2022   
635                          24    PREGÃO ELETRÔNICO          07/2022   
636      00090-00001679/2022-42                               03/2022   
637            00110- 00002366/                               09/2021   

    valor_estimado_contratacao  \
0                   767.907,37   
1                   201.025,16   
2                99.754.200,00   
3                11.703.718,00   
4                   432.163,20   
..                         ...   
633               5.257.461,51   
634               5.899.518,69   
635                  70.000,00   
636                              
637              51.518.031,96   

                                                  text  \
0    AVISOS DE LICITACOES PREGAO ELETRONICO No 116/...   
1    PREGAO ELETRONICO No 129/2018 OBJETO : Registr...   
2    AVISOS DE LICITACOES PREGAO ELETRONICO No 141/...   
3    PREGAO ELETRONICO No 142/ 2018-UASG 925041 Obj...   
4    AVISO DE ABERTURA PREGAO ELETRONICO POR SRP No...   
..                                                 ...   
633  AVISO DE RETIFICAÇÃO ( * ) CONCORRÊNCIA Nº 003...   
634  AVISO CONCORRÊNCIA Nº 02/2022 Processo : 00113...   
635  AVISO DE LICITAÇÃO PREGÃO ELETRÔNICO Nº 07/202...   
636  AVISO DE LICITAÇÃO - CONCORRÊNCIA Nº 03/2022 A...   
637  AVISO DE RETOMADA DA LICITAÇÃO Concorrência nº...   

                                                labels  
0    O O O B-modalidade_licitacao I-modalidade_lici...  
1    B-modalidade_licitacao I-modalidade_licitacao ...  
2    O O O B-modalidade_licitacao I-modalidade_lici...  
3    B-modalidade_licitacao I-modalidade_licitacao ...  
4    O O O B-modalidade_licitacao I-modalidade_lici...  
..                                                 ...  
633  O O O O O O O O B-numero_licitacao O O B-proce...  
634  O O O B-numero_licitacao O O B-processo_gdf I-...  
635  O O O B-modalidade_licitacao I-modalidade_lici...  
636  O O O O O O B-numero_licitacao O O O O O O O O...  
637  O O O O O O O B-numero_licitacao O O O O O O O...  

[638 rows x 6 columns]

In [20]:
# converting to CSV file
data_label.to_csv("./CSVs/V1/AVISO_LICITACAO_SUPERVISAO_FRACA.csv")

In [21]:
corpus = skw.get_IOB()

In [22]:
corpus

[['AVISOS O',
  'DE O',
  'LICITACOES O',
  'PREGAO B-modalidade_licitacao',
  'ELETRONICO I-modalidade_licitacao',
  'No O',
  '116/2018 B-numero_licitacao',
  'OBJETO O',
  ': O',
  'Registro O',
  'de O',
  'Precos O',
  'visando O',
  'a O',
  'eventual O',
  'aquisicao O',
  'de O',
  'Material O',
  'de O',
  'Expediente O',
  '; O',
  'Material O',
  'de O',
  'Acondicionamento O',
  'e O',
  'Embalagem O',
  '; O',
  'Material O',
  'de O',
  'Limpeza O',
  'e O',
  'Producao O',
  'de O',
  'Higienizacao O',
  '; O',
  'Material O',
  'de O',
  'Protecao O',
  'e O',
  'Seguranca O',
  '; O',
  'Ferramenta O',
  '; O',
  'Uniformes O',
  ', O',
  'Tecidos O',
  'e O',
  'Aviamentos O',
  '; O',
  'e O',
  'aquisicao O',
  'de O',
  'equipamentos O',
  'e O',
  'material O',
  'permanente O',
  ': O',
  'Aparelho O',
  'de O',
  'Medicao O',
  'e O',
  'Orientacao O',
  ', O',
  'a O',
  'fim O',
  'de O',
  'atender O',
  'aos O',
  'diversos O',
  'orgaos O',
  'integrantes O

In [23]:
termos_skweak = []
debug=set()
labels_skweak = []
for ato in corpus:
    x = []
    y = []
    for termo in ato:
        termo_label = termo.split()
        x.append(termo_label[0])
        y.append(termo_label[1])
        classes=debug.add(termo_label[1])
    termos_skweak.append(x)
    labels_skweak.append(y)

In [24]:
debug

{'B-modalidade_licitacao',
 'B-numero_licitacao',
 'B-processo_gdf',
 'B-valor_estimado_contratacao',
 'I-modalidade_licitacao',
 'I-processo_gdf',
 'O'}

In [25]:
#Retira da lista aninhada
termos_skweak_list = []
for i in termos_skweak:
   if not isinstance(i, list):
      termos_skweak_list.append(i)
   else:
      for j in i:
        termos_skweak_list.append(j)

len(termos_skweak_list)

111438

In [26]:
#termos_skweak_list

In [27]:
#Retira da lista aninhada
labels_skweak_list = []
for i in labels_skweak:
   if not isinstance(i, list):
      labels_skweak_list.append(i)
   else:
      for j in i:
        labels_skweak_list.append(j)

len(labels_skweak_list)

111438

In [28]:
#Retira da lista aninhada
corpus_skweak_list = []
for i in corpus:
   if not isinstance(i, list):
      corpus_skweak_list.append(i)
   else:
      for j in i:
         corpus_skweak_list.append(j)
#print(corpus_skweak_list)
len(corpus_skweak_list)

111438

In [29]:
#APLICA O TOKENIZADOR EXTRAIR O IOB DA BASE GOLD
# return_df=False para retornar atos e labels, ou  return_df=True para retornar dataset
from iob_transformer import iob_transformer
iob = iob_transformer('id_ato','texto','tipo_ent', keep_punctuation=False, return_df=False)

/Users/lucelia/Documents/GitHub/experiments/members/lucelia/venv/lib/python3.9/site-packages/spacy/language.py:1895: UserWarning: [W123] Argument disable with value ['parser', 'ner'] is used instead of ['senter'] as specified in the config. Be aware that this might affect other components in your pipeline.
  warnings.warn(


In [30]:
atos, labels = iob.transform(tipo_ato)

In [31]:
#Retira da lista aninhada
labels_list = []
for i in labels:
   if not isinstance(i, list):
      labels_list.append(i)
   else:
      for j in i:
         labels_list.append(j)
len(labels_list)

111438

In [32]:
#labels_list

In [33]:
#Retira da lista aninhada
atos_list = []
for i in atos:
   if not isinstance(i, list):
      atos_list.append(i)
   else:
      for j in i:
         atos_list.append(j)
len(atos_list)

111438

In [34]:
#compara se houve quebra após a tokenização
resultados = []
for ato_sk_list , label_sk_list, ato_gold, label_gold in zip(termos_skweak_list, labels_skweak_list,  atos_list, labels_list):
    tupla=(ato_sk_list , label_sk_list, ato_gold, label_gold)
    resultados.append(tupla)
    if ato_sk_list != ato_gold:
        print(ato_sk_list, ato_gold)
for item in resultados:
    print(item)

('AVISOS', 'O', 'AVISOS', 'O')
('DE', 'O', 'DE', 'O')
('LICITACOES', 'O', 'LICITACOES', 'O')
('PREGAO', 'B-modalidade_licitacao', 'PREGAO', 'B-modalidade_licitacao')
('ELETRONICO', 'I-modalidade_licitacao', 'ELETRONICO', 'I-modalidade_licitacao')
('No', 'O', 'No', 'O')
('116/2018', 'B-numero_licitacao', '116/2018', 'B-numero_licitacao')
('OBJETO', 'O', 'OBJETO', 'O')
(':', 'O', ':', 'O')
('Registro', 'O', 'Registro', 'B-objeto_licitacao')
('de', 'O', 'de', 'I-objeto_licitacao')
('Precos', 'O', 'Precos', 'I-objeto_licitacao')
('visando', 'O', 'visando', 'I-objeto_licitacao')
('a', 'O', 'a', 'I-objeto_licitacao')
('eventual', 'O', 'eventual', 'I-objeto_licitacao')
('aquisicao', 'O', 'aquisicao', 'I-objeto_licitacao')
('de', 'O', 'de', 'I-objeto_licitacao')
('Material', 'O', 'Material', 'I-objeto_licitacao')
('de', 'O', 'de', 'I-objeto_licitacao')
('Expediente', 'O', 'Expediente', 'I-objeto_licitacao')
(';', 'O', ';', 'I-objeto_licitacao')
('Material', 'O', 'Material', 'I-objeto_licitacao

In [35]:
#Compara os labels reais e os preditos para avalir a rotulação fraca

#labels_skweak = labels
numero_contrato = 0
numero_contrato_total = 0
B_numero_contrato = 0
numero_contrato_gold=[]

data_assinatura_contrato = 0
data_assinatura_contrato_total = 0
B_data_assinatura_contrato = 0
data_assinatura_contrato_gold = []

processo_gdf = 0
processo_gdf_total = 0
B_processo_gdf = 0
processo_gdf_gold = []

unidade_orcamentaria = 0
unidade_orcamentaria_total = 0
B_unidade_orcamentaria = 0
unidade_orcamentaria_gold = []
teste=[]

programa_trabalho = 0
programa_trabalho_total = 0
B_programa_trabalho = 0
programa_trabalho_gold = []

#for text_sk, label_skweak, text_gold,  label_gold in zip(termos_skweak, labels_skweak, atos, labels):
for ato_sk , label_sk, ato_gold, label_gold in zip(termos_skweak_list, labels_skweak_list,  atos_list, labels_list):    
    #for text_skw, termo_skweak, text_ato, termo_gold in zip(text_sk, label_skweak, text_gold,  label_gold ):
       
       #print("termo swkeak", termo_skweak) 
       if label_gold == "B-numero_contrato":
           #print("Teste")
           numero_contrato_total+=1
           B_numero_contrato=label_gold
           if label_gold == label_sk:
               numero_contrato+=1
           else:
               numero_contrato_gold.append(ato_gold)

       elif label_gold == "B-data_escrito":    
            data_assinatura_contrato_total+=1
            B_data_assinatura_contrato=label_gold
            if label_gold == label_sk:
                data_assinatura_contrato+=1
            else:
                data_assinatura_contrato_gold.append(ato_gold)
       
       elif label_gold == "B-processo_gdf":        
            processo_gdf_total+=1
            B_processo_gdf=label_gold
            if label_gold == label_sk:
                processo_gdf+=1
            else:
                processo_gdf_gold.append(ato_gold)         
                

       elif label_gold == "B-unidade_orcamentaria":     
            unidade_orcamentaria_total+=1
            B_unidade_orcamentaria=label_gold
            if label_gold == label_sk:
                unidade_orcamentaria+=1
                
            else:
                unidade_orcamentaria_gold.append(ato_gold) 
                 
       elif label_gold == "B-programa_trabalho":  
            programa_trabalho_total+=1
            B_programa_trabalho=label_gold
            if label_gold == label_sk:
                programa_trabalho+=1
            else:
                programa_trabalho_gold.append(ato_gold)                
print("Tipo da entidade             Total Entidade Gold                 Total Entidade Skweak")                
#print("B-numero_contrato",              "   ",numero_contrato_total,         "   ",numero_contrato,"      ","       ",numero_contrato_gold)
#print("B-data_assinatura_contrato"," ",data_assinatura_contrato_total,"   ",data_assinatura_contrato,"      ",data_assinatura_contrato_gold)
print("B-processo_gdf"," ", processo_gdf_total,"   ",processo_gdf,"      ",processo_gdf_gold)

#print("B-unidade_orcamentaria",      "  ",unidade_orcamentaria_total,    "   ",unidade_orcamentaria)#,"          ",unidade_orcamentaria_gold)
#print( "B-programa_trabalho",       "  ",programa_trabalho_total,       "   ",programa_trabalho)#,"             ",programa_trabalho_gold)

#print(programa_trabalho_gold)

Tipo da entidade             Total Entidade Gold                 Total Entidade Skweak
B-processo_gdf   598     589        ['00080-00029272/', '00080-', '974002', 'PREGAO', '00431-00002015/', 'PREGAO', 'JULIANA', 'Processo', '00080-00159144/']


In [36]:
#Atos e rótulos supervisão fraca
X=termos_skweak
y=labels_skweak

In [37]:
#Split da base rotulada pela Supervisão Fraca para pegar o train e treinar o CRF
# 80% treino, 20% teste

from sklearn.model_selection import train_test_split
x_train, x_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=None, shuffle=False)
print( 'x_train',len(x_train),'\n','x_test',len(x_test),'\n','total atos',len(x))

x_train 510 
 x_test 128 
 total atos 240


In [38]:
''' x_train = []
for i in x:
   if not isinstance(i, list):
      x_train.append(i)
   else:
      for j in i:
         x_train.append(j)
         
y_train = []
for i in y:
   if not isinstance(i, list):
      y_train.append(i)
   else:
      for j in i:
         y_train.append(j) '''

' x_train = []\nfor i in x:\n   if not isinstance(i, list):\n      x_train.append(i)\n   else:\n      for j in i:\n         x_train.append(j)\n         \ny_train = []\nfor i in y:\n   if not isinstance(i, list):\n      y_train.append(i)\n   else:\n      for j in i:\n         y_train.append(j) '

In [39]:
#Lista quais entidades estão no x_train

#Retira da lista aninhada
ato_list = []
for i in x_train:
   if not isinstance(i, list):
      ato_list.append(i)
   else:
      for j in i:
         ato_list.append(j)
label_list = []
for i in y_train:
   if not isinstance(i, list):
      label_list.append(i)
   else:
      for j in i:
        label_list.append(j)

teste=  []
for ato, label in zip(ato_list,label_list):
    tupla=(ato,label)
    teste.append(tupla)

#teste

In [40]:
#Carrega os atos do dataset de teste da base ouro
#https://pt.stackoverflow.com/questions/232208/ler-uma-lista-de-listas-em-txt-python-3
import pickle
#Suspensão
#with open("./CSVs/V1/Suspensao_Licitacao_Split_0_x_test.txt", "rb") as file:
#Anul Revog
with open("./CSVs/V1/Aviso_Licitacao_Split_0_x_test.txt", "rb") as file:
    x_test = pickle.load(file)

In [41]:
#Carrega os labels do dataset de teste da base ouro
import pickle
#Suspensao
#with open("./CSVs/V1/Suspensao_Licitacao_Split_0_y_test.txt", "rb") as file:
#Anul e Revog
with open("./CSVs/V1/Aviso_Licitacao_Split_0_y_test.txt", "rb") as file:    
    y_test = pickle.load(file)

In [42]:
#Lista quais entidades estão no x_teste

#Retira da lista aninhada

x_test_list = []
for i in x_test:
   if not isinstance(i, list):
      x_test_list.append(i)
   else:
      for j in i:
        x_test_list.append(j)

#Retira da lista aninhada
y_test_list = []
for i in y_test:
   if not isinstance(i, list):
      y_test_list.append(i)
   else:
      for j in i:
       y_test_list.append(j)



teste =  []
for ato, label in zip(x_test_list,y_test_list):
    tupla=(ato,label)
    teste.append(tupla)
#teste

CRF

In [43]:
#X_train

def get_features(sentence):
        """Create features for each word in act.
        Create a list of dict of words features to be used in the predictor module.
        Args:
            act (list): List of words in an act.
        Returns:
            A list with a dictionary of features for each of the words.
        """
        sent_features = []
        
        for i in range(len(sentence)):
            word_feat = {
                'word': sentence[i].lower(),
                'capital_letter': sentence[i][0].isupper(),
                'all_capital': sentence[i].isupper(),
                'isdigit': sentence[i].isdigit(),
                'word_before': sentence[i].lower() if i == 0 else sentence[i-1].lower(),
                'word_after:': sentence[i].lower() if i+1 >= len(sentence) else sentence[i+1].lower(),
                'BOS': i == 0,
                'EOS': i == len(sentence)-1
            }
            sent_features.append(word_feat)
        return sent_features
    
for i in range(len(x_train)):
    x_train[i] = get_features(x_train[i])

In [44]:
#X_test
def get_features(sentence):
        """Create features for each word in act.
        Create a list of dict of words features to be used in the predictor module.
        Args:
            act (list): List of words in an act.
        Returns:
            A list with a dictionary of features for each of the words.
        """
        x_test = []
        sent_features = []
        for i in range(len(sentence)):
            word_feat = {
                'word': sentence[i].lower(),
                'capital_letter': sentence[i][0].isupper(),
                'all_capital': sentence[i].isupper(),
                'isdigit': sentence[i].isdigit(),
                'word_before': sentence[i].lower() if i == 0 else sentence[i-1].lower(),
                'word_after:': sentence[i].lower() if i+1 >= len(sentence) else sentence[i+1].lower(),
                'BOS': i == 0,
                'EOS': i == len(sentence)-1
            }
            sent_features.append(word_feat)
        return sent_features
    
for i in range(len(x_test)):
    x_test[i] = get_features(x_test[i])

In [45]:
import sklearn_crfsuite
from sklearn_crfsuite import metrics


crf = sklearn_crfsuite.CRF(
    algorithm='lbfgs',
    c1=0.1,
    c2=0.1,
    max_iterations=100,
     
    all_possible_transitions=False,
    all_possible_states=True
)

#crf.fit(x_train, y_train)

try:
    #crf.fit(x_train[:200], y_train[:200])
    crf.fit(x_train, y_train)
except AttributeError:
    pass


In [46]:
#import eli5
#eli5.show_weights(crf, top=30)
#eli5.show_weights(crf, top=5, show=['transition_features'])

In [47]:
crf.classes_

['O',
 'B-modalidade_licitacao',
 'I-modalidade_licitacao',
 'B-numero_licitacao',
 'B-valor_estimado_contratacao',
 'B-processo_gdf',
 'I-processo_gdf']

In [48]:
#Rotulação baseada no modelo treinado com supervisão fraca
classes = list(crf.classes_)
classes.remove('O')

y_pred = crf.predict(x_test)
metrics.flat_f1_score(y_test, y_pred, average='weighted', labels=classes)

0.8973473354788906

In [49]:
y_pred_list = []
for i in y_pred:
   if not isinstance(i, list):
      y_pred_list.append(i)
   else:
      for j in i:
       y_pred_list.append(j)

len(y_pred_list)

21669

In [50]:
resultados = []
for ato_gold, label_gold, label_pred in zip(x_test_list, y_test_list, y_pred_list):
    
   if (label_gold != label_pred) and (label_gold in ['B-modalidade_licitacao', 'B-numero_licitacao', 'B-processo_gdf', 'I-modalidade_licitacao', 'I-numero_licitacao', 'I-processo_gdf' ]):
   #    print(label_gold, label_pred)
        tupla=(ato_gold,  label_gold, label_pred)
        resultados.append(tupla)
#print(resultados)
for item in resultados:
    print(item)

('Procedimento', 'B-modalidade_licitacao', 'O')
('Licitatório', 'I-modalidade_licitacao', 'O')
('Eletrônico', 'I-modalidade_licitacao', 'O')
('053/2021', 'B-numero_licitacao', 'O')
('00050-00031571/', 'B-processo_gdf', 'O')
('2020-61', 'I-processo_gdf', 'O')
('37/2021', 'B-numero_licitacao', 'O')
('15/2021', 'B-numero_licitacao', 'O')
('Concorrência', 'B-modalidade_licitacao', 'O')
('08/2021', 'B-numero_licitacao', 'O')
('Procedimento', 'B-modalidade_licitacao', 'O')
('Licitatório', 'I-modalidade_licitacao', 'O')
('Eletrônico', 'I-modalidade_licitacao', 'O')
('019/2020', 'B-numero_licitacao', 'O')
('00111-00000455/', 'B-processo_gdf', 'O')
('2020-75', 'I-processo_gdf', 'O')
('03/2021', 'B-numero_licitacao', 'O')
('00111-00003425/', 'B-processo_gdf', 'O')
('2021-00', 'I-processo_gdf', 'O')
('Licitação', 'B-modalidade_licitacao', 'O')
('Presencial', 'I-modalidade_licitacao', 'O')
('17/2021', 'B-numero_licitacao', 'O')
('08/2021', 'B-numero_licitacao', 'O')
('CONCORRÊNCIA', 'B-modalidade_

In [53]:
import numpy as np
from seqeval.metrics import classification_report
from seqeval.scheme import IOB2
from seqeval.metrics import f1_score

report = classification_report(y_test, y_pred, output_dict=False, mode='strict', scheme=IOB2)
print(report)
np.save("./Results/V1/METRICA_AVISO_LICITACAO_SKWEAK_0.npy", report)

                                  precision    recall  f1-score   support

codigo_licitacao_sistema_compras       0.00      0.00      0.00        91
         data_abertura_licitacao       0.00      0.00      0.00       127
            modalidade_licitacao       0.98      0.81      0.89       139
                nome_responsavel       0.00      0.00      0.00       129
                numero_licitacao       0.98      0.80      0.88       143
                objeto_licitacao       0.00      0.00      0.00       111
                 orgao_licitante       0.00      0.00      0.00       101
                    processo_gdf       0.93      0.88      0.90       121
                 sistema_compras       0.00      0.00      0.00       158
                     tipo_objeto       0.00      0.00      0.00        31
      valor_estimado_contratacao       0.97      0.78      0.86        98

                       micro avg       0.97      0.33      0.49      1249
                       macro avg    

In [52]:
report = metrics.flat_classification_report(
    #y_test[:200], y_pred[:200], labels=classes, digits=3))
   gold_y_test, y_pred, labels=classes, digits=3, output_dict=False)
print(report)

NameError: name 'gold_y_test' is not defined

In [ ]:
#output_dict=True gerar a saída para gravar no results

import numpy as np
report = metrics.flat_classification_report(
    #y_test[:200], y_pred[:200], labels=classes, digits=3))
    gold_y_test, y_pred, labels=classes, digits=3, output_dict=True)
print(report)
np.save("./Results/METRICA_EXTRATO_CONTRATO_SKWEAK_V1_0.npy", report)

In [ ]:
# CODIGO DE APLICACAO DO MODELO CRF TREINADO

#import dodfCRF
#crf = dodfCRF.CRFContratos()
#crf.init_model_from_path("contratosFINAL.pkl")
#crfIOB = crf.model_predict(dados)